### Import Required Libraries and Set Up Environment Variables

In [1]:
# Dependencies
import requests
import time
from dotenv import load_dotenv
import os
import pandas as pd
from pandas import json_normalize
import json

In [2]:
# Set environment variables from the .env in the local environment
load_dotenv()

nyt_api_key = os.getenv("NYT_KEY")
tmdb_api_key = os.getenv("TMDB_KEY")

### Access the New York Times API

In [3]:
# Set the base URL
nyt_base_url = "https://api.nytimes.com/svc/search/v2/articlesearch.json?"

# Filter for movie reviews with "love" in the headline
# section_name should be "Movies"
# type_of_material should be "Review"
filter_query = 'section_name:"Movies" AND type_of_material:"Review" AND headline:"love"'

# Use a sort filter, sort by newest
sort = "newest"

# Select the following fields to return:
# headline, web_url, snippet, source, keywords, pub_date, byline, word_count
field_list = "headline,web_url,snippet,source,keywords,pub_date,byline,word_count"

# Search for reviews published between a begin and end date
begin_date = "20130101"
end_date = "20230531"

# Build URL
nyt_query_url = (
    f"{nyt_base_url}api-key={nyt_api_key}&begin_date={begin_date}&end_date={end_date}"
    + f'&fq={filter_query}&sort={sort}&fl={field_list}'
)

In [4]:
# Create an empty list to store the reviews
reviews_list = []

# loop through pages 0-19
for page_of_reviews in range(0,20):
    # create query with a page number
    # API results show 10 articles at a time
    nyt_query_url = nyt_query_url + f"&page={page_of_reviews + 1}"
    
    # Make a "GET" request and retrieve the JSON
    response = requests.get(nyt_query_url)
    page_of_reviews = response.json()
    # Add a twelve second interval between queries to stay within API query limits
    # placing this after the other for loop
    # Print the page number that had no results then break from the loop
    if len(page_of_reviews["response"]["docs"]) == 0:
        print(f"Page {page} had no reviews")
        break
    # Try and save the reviews to the reviews_list
    for review in page_of_reviews["response"]["docs"]:
        # loop through the reviews["response"]["docs"] and append each review to the list
        reviews_list.append(review)
        # Print the page that was just retrieved
        print(json.dumps(page_of_reviews, indent=4))
        # Print the page number that had no results then break from the loop
        # This makes no sense to put in here, placing that above.
    time.sleep(12)

{
    "status": "OK",
    "copyright": "Copyright (c) 2024 The New York Times Company. All Rights Reserved.",
    "response": {
        "docs": [
            {
                "web_url": "https://www.nytimes.com/2023/01/31/movies/pamela-a-love-story-review.html",
                "snippet": "This documentary from Ryan White rewinds, to powerful effect, on Pamela Anderson\u2019s life and fame.",
                "source": "The New York Times",
                "headline": {
                    "main": "\u2018Pamela, a Love Story\u2019 Review: A Frank Look Back",
                    "kicker": null,
                    "content_kicker": null,
                    "print_headline": "Pamela, a Love Story",
                    "name": null,
                    "seo": null,
                    "sub": null
                },
                "keywords": [
                    {
                        "name": "subject",
                        "value": "Documentary Films and Programs",
             

In [5]:
# Preview the first 5 results in JSON format
# Use json.dumps with argument indent=4 to format data
    # Why am I previewing data after saving it :(
print(json.dumps(reviews_list[:5], indent=4))

[
    {
        "web_url": "https://www.nytimes.com/2023/01/31/movies/pamela-a-love-story-review.html",
        "snippet": "This documentary from Ryan White rewinds, to powerful effect, on Pamela Anderson\u2019s life and fame.",
        "source": "The New York Times",
        "headline": {
            "main": "\u2018Pamela, a Love Story\u2019 Review: A Frank Look Back",
            "kicker": null,
            "content_kicker": null,
            "print_headline": "Pamela, a Love Story",
            "name": null,
            "seo": null,
            "sub": null
        },
        "keywords": [
            {
                "name": "subject",
                "value": "Documentary Films and Programs",
                "rank": 1,
                "major": "N"
            },
            {
                "name": "persons",
                "value": "Anderson, Pamela (1967- )",
                "rank": 2,
                "major": "N"
            },
            {
                "name": "persons",

In [30]:
# Convert reviews_list to a Pandas DataFrame using json_normalize()
df = json_normalize(reviews_list)
df.head()

web_url  \
0  https://www.nytimes.com/2023/01/31/movies/pame...   
1  https://www.nytimes.com/2023/01/19/movies/in-f...   
2  https://www.nytimes.com/2023/01/19/movies/afte...   
3  https://www.nytimes.com/2023/01/05/movies/alca...   
4  https://www.nytimes.com/2022/12/15/movies/nell...   

                                             snippet              source  \
0  This documentary from Ryan White rewinds, to p...  The New York Times   
1  In Matt Carter’s gay rugby film, sports and ro...  The New York Times   
2  In this intelligent melodrama by the director ...  The New York Times   
3  In this naturalistic drama from Spain, a famil...  The New York Times   
4  A family archive provides intimate records of ...  The New York Times   

                                            keywords  \
0  [{'name': 'subject', 'value': 'Documentary Fil...   
1  [{'name': 'subject', 'value': 'Movies', 'rank'...   
2  [{'name': 'subject', 'value': 'Movies', 'rank'...   
3  [{'name': 'subject', 'value': 'Movies', 'rank'...   
4  [{'name': 'subject', 'value': 'Documentary Fil...   

                   pub_date  word_count  \
0  2023-01-31T12:00:05+0000         295   
1  2023-01-19T17:50:16+0000         281   
2  2023-01-19T12:00:06+0000         359   
3  2023-01-05T12:00:03+0000         306   
4  2022-12-15T12:00:04+0000         308   

                                       headline.main headline.kicker  \
0   ‘Pamela, a Love Story’ Review: A Frank Look Back            None   
1  ‘In From the Side’ Review: Love and Rugby Play...            None   
2               ‘After Love’ Review: The Other Woman   Critic’s Pick   
3                   ‘Alcarràs’ Review: Labor of Love            None   
4  ‘Nelly & Nadine’ Review: An Unlikely Love, an ...            None   

  headline.content_kicker headline.print_headline headline.name headline.seo  \
0                    None    Pamela, a Love Story          None         None   
1                    None        In From the Side          None         None   
2                    None              After Love          None         None   
3                    None                Alcarràs          None         None   
4                    None      Nelly &amp; Nadine          None         None   

  headline.sub     byline.original  \
0         None      By Glenn Kenny   
1         None      By Kyle Turner   
2         None  By Beatrice Loayza   
3         None    By Devika Girish   
4         None       By Teo Bugbee   

                                       byline.person byline.organization  
0  [{'firstname': 'Glenn', 'middlename': None, 'l...                None  
1  [{'firstname': 'Kyle', 'middlename': None, 'la...                None  
2  [{'firstname': 'Beatrice', 'middlename': None,...                None  
3  [{'firstname': 'Devika', 'middlename': None, '...                None  
4  [{'firstname': 'Teo', 'middlename': None, 'las...                None

In [31]:
# Extract the title from the "headline.main" column and
# df.columns
# save it to a new column "title"
df["title"] = df["headline.main"]
# df.head()
# Title is between unicode characters \u2018 and \u2019. 
# def extract_content(input_string):
#     start_index = input_string.find('\u2018')
#     end_index = input_string.find(' Review') + len(' Review')`
    
#     if start_index != -1 and end_index != -1:
#         return input_string[start_index:end_index]
#     else:
#         return "Pattern not found."
# df["title_trimmed"] = df["title"].str.replace(' Review', '')
def extract_content(input_string):
    start_index = input_string.find('\u2018')
    end_index = input_string.find('\u2019 Review')
    
    if start_index != -1 and end_index != -1:
        return input_string[start_index+1:end_index]
    else:
        return "Pattern not found."
df["title"] = df["title"].apply(extract_content)

df.head()
# End string should include " Review" to avoid cutting title early
# No it should not :(. It makes matching horrible and the results for movie search poor
print(df.iloc[0]["keywords"])

[{'name': 'subject', 'value': 'Documentary Films and Programs', 'rank': 1, 'major': 'N'}, {'name': 'persons', 'value': 'Anderson, Pamela (1967- )', 'rank': 2, 'major': 'N'}, {'name': 'persons', 'value': 'White, Ryan (Filmmaker)', 'rank': 3, 'major': 'N'}, {'name': 'creative_works', 'value': 'Pamela, a Love Story (Movie)', 'rank': 4, 'major': 'N'}]


In [32]:
# Extract 'name' and 'value' from items in "keywords" column
def extract_keywords(keyword_list):
    extracted_keywords = ""
    for item in keyword_list:
        # Extract 'name' and 'value'
        keyword = f"{item['name']}: {item['value']};" 
        # Append the keyword item to the extracted_keywords list
        extracted_keywords += keyword
    return extracted_keywords

# Fix the "keywords" column by converting cells from a list to a string
df["keywords"] = df["keywords"].apply(extract_keywords)
df.head()

web_url  \
0  https://www.nytimes.com/2023/01/31/movies/pame...   
1  https://www.nytimes.com/2023/01/19/movies/in-f...   
2  https://www.nytimes.com/2023/01/19/movies/afte...   
3  https://www.nytimes.com/2023/01/05/movies/alca...   
4  https://www.nytimes.com/2022/12/15/movies/nell...   

                                             snippet              source  \
0  This documentary from Ryan White rewinds, to p...  The New York Times   
1  In Matt Carter’s gay rugby film, sports and ro...  The New York Times   
2  In this intelligent melodrama by the director ...  The New York Times   
3  In this naturalistic drama from Spain, a famil...  The New York Times   
4  A family archive provides intimate records of ...  The New York Times   

                                            keywords  \
0  subject: Documentary Films and Programs;person...   
1  subject: Movies;creative_works: In From the Si...   
2  subject: Movies;creative_works: After Love (20...   
3  subject: Movies;persons: Simon, Carla;creative...   
4  subject: Documentary Films and Programs;person...   

                   pub_date  word_count  \
0  2023-01-31T12:00:05+0000         295   
1  2023-01-19T17:50:16+0000         281   
2  2023-01-19T12:00:06+0000         359   
3  2023-01-05T12:00:03+0000         306   
4  2022-12-15T12:00:04+0000         308   

                                       headline.main headline.kicker  \
0   ‘Pamela, a Love Story’ Review: A Frank Look Back            None   
1  ‘In From the Side’ Review: Love and Rugby Play...            None   
2               ‘After Love’ Review: The Other Woman   Critic’s Pick   
3                   ‘Alcarràs’ Review: Labor of Love            None   
4  ‘Nelly & Nadine’ Review: An Unlikely Love, an ...            None   

  headline.content_kicker headline.print_headline headline.name headline.seo  \
0                    None    Pamela, a Love Story          None         None   
1                    None        In From the Side          None         None   
2                    None              After Love          None         None   
3                    None                Alcarràs          None         None   
4                    None      Nelly &amp; Nadine          None         None   

  headline.sub     byline.original  \
0         None      By Glenn Kenny   
1         None      By Kyle Turner   
2         None  By Beatrice Loayza   
3         None    By Devika Girish   
4         None       By Teo Bugbee   

                                       byline.person byline.organization  \
0  [{'firstname': 'Glenn', 'middlename': None, 'l...                None   
1  [{'firstname': 'Kyle', 'middlename': None, 'la...                None   
2  [{'firstname': 'Beatrice', 'middlename': None,...                None   
3  [{'firstname': 'Devika', 'middlename': None, '...                None   
4  [{'firstname': 'Teo', 'middlename': None, 'las...                None   

                  title  
0  Pamela, a Love Story  
1      In From the Side  
2            After Love  
3              Alcarràs  
4        Nelly & Nadine

In [33]:
# Create a list from the "title" column using to_list()
# These titles will be used in the query for The Movie Database
titles_list = df["title"].to_list()
print(titles_list[:5])
print(len(titles_list))

['Pamela, a Love Story', 'In From the Side', 'After Love', 'Alcarràs', 'Nelly & Nadine']
200


### Access The Movie Database API

In [34]:
# Prepare The Movie Database query
tmdb_movie_query_url = "https://api.themoviedb.org/3/search/movie?query="
tmdb_key_string = "&api_key=" + tmdb_api_key

In [35]:
# Create an empty list to store the results
tmdb_movies_list = []

# Create a request counter to sleep the requests after a multiple
# of 50 requests
request_counter = 0
def batch_requests(batch_size):
    if request_counter % batch_size == 0 and request_counter != 0:
        time.sleep(12)
    

# Loop through the titles
for index, title in enumerate(titles_list):
    # Check if we need to sleep before making a request
    batch_requests(index + 1)

    # Add 1 to the request counter
    request_counter+=1
    
    # Perform a "GET" request for The Movie Database
    tmdb_query_url = tmdb_movie_query_url+title+tmdb_key_string
    tmdb_query_response = requests.get(tmdb_query_url)
    tmdb_query_response = tmdb_query_response.json()

    # Include a try clause to search for the full movie details.
    # Use the except clause to print out a statement if a movie
    # is not found.
    try:
        # Get movie id
        movie_id = tmdb_query_response["results"][0]["id"]
        
        # Make a request for a the full movie details
        single_movie_url = f"https://api.themoviedb.org/3/movie/{movie_id}?api_key={tmdb_api_key}"

        # Execute "GET" request with url
        movie_response = requests.get(single_movie_url)
        movie_response = movie_response.json()
        # Extract the genre names into a list
        
        genre_names = []
        for genre in movie_response["genres"]:
            genre_names.append(genre["name"])
        
        # Extract the spoken_languages' English name into a list
        language_names = []
        for language in movie_response["spoken_languages"]:
            language_names.append(language["english_name"])
        # Extract the production_countries' name into a list
        production_countries = []
        for country in movie_response["production_countries"]:
            production_countries.append(country["name"])
        # Add the relevant data to a dictionary and
        # append it to the tmdb_movies_list list
        movie_data = {"title":movie_response["title"],"genres":genre_names,"languages": language_names,"production_countries": production_countries}
        tmdb_movies_list.append(movie_data)

    except KeyError as e:
    # Handling the KeyError
        print(f"KeyError: {e}. The key does not exist in the dictionary.")
    except IndexError as e:
        print(f"IndexError: {e}. The index does not exist.")
    except Exception as e:
        print(f"Movie not found for title: {title}", e)
        # Print out the title that was found
    else:
        print(f"Movie:{title} Found")
    



Movie:Pamela, a Love Story Found
Movie:In From the Side Found
Movie:After Love Found
Movie:Alcarràs Found
Movie:Nelly & Nadine Found
Movie:Lady Chatterley’s Lover Found
Movie:The Sound of Christmas Found
Movie:The Inspection Found
Movie:Bones and All Found
Movie:My Policeman Found
Movie:Pamela, a Love Story Found
Movie:In From the Side Found
Movie:After Love Found
Movie:Alcarràs Found
Movie:Nelly & Nadine Found
Movie:Lady Chatterley’s Lover Found
Movie:The Sound of Christmas Found
Movie:The Inspection Found
Movie:Bones and All Found
Movie:My Policeman Found
Movie:Pamela, a Love Story Found
Movie:In From the Side Found
Movie:After Love Found
Movie:Alcarràs Found
Movie:Nelly & Nadine Found
Movie:Lady Chatterley’s Lover Found
Movie:The Sound of Christmas Found
Movie:The Inspection Found
Movie:Bones and All Found
Movie:My Policeman Found
Movie:Pamela, a Love Story Found
Movie:In From the Side Found
Movie:After Love Found
Movie:Alcarràs Found
Movie:Nelly & Nadine Found
Movie:Lady Chatterley

In [36]:
# Preview the first 5 results in JSON format
print(tmdb_movies_list[:5])
# Use json.dumps with argument indent=4 to format data
json.dumps(tmdb_movies_list, indent=4)

[{'title': 'Pamela, A Love Story', 'genres': ['Documentary'], 'languages': ['English'], 'production_countries': ['United States of America']}, {'title': 'In from the Side', 'genres': ['Drama', 'Romance'], 'languages': ['English'], 'production_countries': ['United Kingdom']}, {'title': 'After Love', 'genres': ['Drama'], 'languages': ['English', 'Arabic', 'French', 'Urdu'], 'production_countries': ['United Kingdom']}, {'title': 'Alcarràs', 'genres': ['Drama'], 'languages': ['Catalan'], 'production_countries': ['Spain']}, {'title': 'Nelly and Monsieur Arnaud', 'genres': ['Drama', 'Romance'], 'languages': ['French'], 'production_countries': ['Germany', 'France', 'Italy']}]


'[\n    {\n        "title": "Pamela, A Love Story",\n        "genres": [\n            "Documentary"\n        ],\n        "languages": [\n            "English"\n        ],\n        "production_countries": [\n            "United States of America"\n        ]\n    },\n    {\n        "title": "In from the Side",\n        "genres": [\n            "Drama",\n            "Romance"\n        ],\n        "languages": [\n            "English"\n        ],\n        "production_countries": [\n            "United Kingdom"\n        ]\n    },\n    {\n        "title": "After Love",\n        "genres": [\n            "Drama"\n        ],\n        "languages": [\n            "English",\n            "Arabic",\n            "French",\n            "Urdu"\n        ],\n        "production_countries": [\n            "United Kingdom"\n        ]\n    },\n    {\n        "title": "Alcarr\\u00e0s",\n        "genres": [\n            "Drama"\n        ],\n        "languages": [\n            "Catalan"\n        ],\n        "

# Convert the results to a DataFrame


In [39]:
movies = pd.DataFrame(tmdb_movies_list)
movies.head()

title            genres  \
0       Pamela, A Love Story     [Documentary]   
1           In from the Side  [Drama, Romance]   
2                 After Love           [Drama]   
3                   Alcarràs           [Drama]   
4  Nelly and Monsieur Arnaud  [Drama, Romance]   

                         languages        production_countries  
0                        [English]  [United States of America]  
1                        [English]            [United Kingdom]  
2  [English, Arabic, French, Urdu]            [United Kingdom]  
3                        [Catalan]                     [Spain]  
4                         [French]    [Germany, France, Italy]

### Merge and Clean the Data for Export

In [40]:
# Merge the New York Times reviews and TMDB DataFrames on title
merged_df = pd.merge(df, movies, on='title', how='inner')
merged_df.head()

web_url  \
0  https://www.nytimes.com/2023/01/19/movies/afte...   
1  https://www.nytimes.com/2023/01/19/movies/afte...   
2  https://www.nytimes.com/2023/01/19/movies/afte...   
3  https://www.nytimes.com/2023/01/19/movies/afte...   
4  https://www.nytimes.com/2023/01/19/movies/afte...   

                                             snippet              source  \
0  In this intelligent melodrama by the director ...  The New York Times   
1  In this intelligent melodrama by the director ...  The New York Times   
2  In this intelligent melodrama by the director ...  The New York Times   
3  In this intelligent melodrama by the director ...  The New York Times   
4  In this intelligent melodrama by the director ...  The New York Times   

                                            keywords  \
0  subject: Movies;creative_works: After Love (20...   
1  subject: Movies;creative_works: After Love (20...   
2  subject: Movies;creative_works: After Love (20...   
3  subject: Movies;creative_works: After Love (20...   
4  subject: Movies;creative_works: After Love (20...   

                   pub_date  word_count                         headline.main  \
0  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   
1  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   
2  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   
3  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   
4  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   

  headline.kicker headline.content_kicker headline.print_headline  \
0   Critic’s Pick                    None              After Love   
1   Critic’s Pick                    None              After Love   
2   Critic’s Pick                    None              After Love   
3   Critic’s Pick                    None              After Love   
4   Critic’s Pick                    None              After Love   

  headline.name headline.seo headline.sub     byline.original  \
0          None         None         None  By Beatrice Loayza   
1          None         None         None  By Beatrice Loayza   
2          None         None         None  By Beatrice Loayza   
3          None         None         None  By Beatrice Loayza   
4          None         None         None  By Beatrice Loayza   

                                       byline.person byline.organization  \
0  [{'firstname': 'Beatrice', 'middlename': None,...                None   
1  [{'firstname': 'Beatrice', 'middlename': None,...                None   
2  [{'firstname': 'Beatrice', 'middlename': None,...                None   
3  [{'firstname': 'Beatrice', 'middlename': None,...                None   
4  [{'firstname': 'Beatrice', 'middlename': None,...                None   

        title   genres                        languages production_countries  
0  After Love  [Drama]  [English, Arabic, French, Urdu]     [United Kingdom]  
1  After Love  [Drama]  [English, Arabic, French, Urdu]     [United Kingdom]  
2  After Love  [Drama]  [English, Arabic, French, Urdu]     [United Kingdom]  
3  After Love  [Drama]  [English, Arabic, French, Urdu]     [United Kingdom]  
4  After Love  [Drama]  [English, Arabic, French, Urdu]     [United Kingdom]

In [42]:
# Remove list brackets and quotation marks on the columns containing lists
# Create a list of the columns that need fixing
columns_to_fix = ["byline.person", "genres","languages","production_countries"]

# Create a list of characters to remove
characters_to_remove=["[", "]", "u/2018","u/2019"]

def remove_characters(input_string):
    # Use the predefined list of characters_to_remove
    characters_to_remove = ["[", "]", "\u2018", "\u2019"]
    
    # Create a translation table to remove specified characters
    translation_table = str.maketrans('', '', ''.join(characters_to_remove))
    
    # Use translate to remove characters
    result_string = input_string.translate(translation_table)
    
    return result_string
    

# Loop through the list of columns to fix
for column in columns_to_fix:

    # Convert the column to type 'str'
    merged_df[column] = merged_df[column].astype(str)

    # Loop through characters to remove
    merged_df[column] = merged_df[column].apply(remove_characters)
        

# Display the fixed DataFrame
merged_df.head()

web_url  \
0  https://www.nytimes.com/2023/01/19/movies/afte...   
1  https://www.nytimes.com/2023/01/19/movies/afte...   
2  https://www.nytimes.com/2023/01/19/movies/afte...   
3  https://www.nytimes.com/2023/01/19/movies/afte...   
4  https://www.nytimes.com/2023/01/19/movies/afte...   

                                             snippet              source  \
0  In this intelligent melodrama by the director ...  The New York Times   
1  In this intelligent melodrama by the director ...  The New York Times   
2  In this intelligent melodrama by the director ...  The New York Times   
3  In this intelligent melodrama by the director ...  The New York Times   
4  In this intelligent melodrama by the director ...  The New York Times   

                                            keywords  \
0  subject: Movies;creative_works: After Love (20...   
1  subject: Movies;creative_works: After Love (20...   
2  subject: Movies;creative_works: After Love (20...   
3  subject: Movies;creative_works: After Love (20...   
4  subject: Movies;creative_works: After Love (20...   

                   pub_date  word_count                         headline.main  \
0  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   
1  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   
2  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   
3  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   
4  2023-01-19T12:00:06+0000         359  ‘After Love’ Review: The Other Woman   

  headline.kicker headline.content_kicker headline.print_headline  \
0   Critic’s Pick                    None              After Love   
1   Critic’s Pick                    None              After Love   
2   Critic’s Pick                    None              After Love   
3   Critic’s Pick                    None              After Love   
4   Critic’s Pick                    None              After Love   

  headline.name headline.seo headline.sub     byline.original  \
0          None         None         None  By Beatrice Loayza   
1          None         None         None  By Beatrice Loayza   
2          None         None         None  By Beatrice Loayza   
3          None         None         None  By Beatrice Loayza   
4          None         None         None  By Beatrice Loayza   

                                       byline.person byline.organization  \
0  {'firstname': 'Beatrice', 'middlename': None, ...                None   
1  {'firstname': 'Beatrice', 'middlename': None, ...                None   
2  {'firstname': 'Beatrice', 'middlename': None, ...                None   
3  {'firstname': 'Beatrice', 'middlename': None, ...                None   
4  {'firstname': 'Beatrice', 'middlename': None, ...                None   

        title   genres                             languages  \
0  After Love  'Drama'  'English', 'Arabic', 'French', 'Urd'   
1  After Love  'Drama'  'English', 'Arabic', 'French', 'Urd'   
2  After Love  'Drama'  'English', 'Arabic', 'French', 'Urd'   
3  After Love  'Drama'  'English', 'Arabic', 'French', 'Urd'   
4  After Love  'Drama'  'English', 'Arabic', 'French', 'Urd'   

  production_countries  
0     'United Kingdom'  
1     'United Kingdom'  
2     'United Kingdom'  
3     'United Kingdom'  
4     'United Kingdom'

In [16]:
# Drop "byline.person" column
merged_df.drop(columns="byline.person", inplace=True)

In [44]:
# Delete duplicate rows and reset index
df_no_duplicates = merged_df.drop_duplicates()

In [46]:
# Export data to CSV without the index
df_no_duplicates.to_csv("movie_reviews.csv")